In [4]:
require 'net/http'
require 'pp'
require 'json'

class VideoFaceRecog
  def initialize(subscription_key)
    @subscription_key = subscription_key
  end
  
  def start(filepath)
    uri = URI('https://westus.api.cognitive.microsoft.com/video/v1.0/trackface')
    uri.query = URI.encode_www_form({
    })

    request = Net::HTTP::Post.new(uri.request_uri)
    request['Content-Type'] = 'application/octet-stream'
    request['Ocp-Apim-Subscription-Key'] = @subscription_key
    request.body = File.open(filepath, 'rb').read

    response = Net::HTTP.start(uri.host, uri.port, :use_ssl => uri.scheme == 'https') do |http|
      http.request(request)
    end
    
    @operation_location_url = response.header.get_fields('Operation-Location')[0]
  end
  
  def result(operation_location_url)
    @operation_location_url ||= operation_location_url
    uri = URI(@operation_location_url)

    request = Net::HTTP::Get.new(uri.request_uri)
    request['Content-Type'] = 'application/json'
    request['Ocp-Apim-Subscription-Key'] = @subscription_key

    response = Net::HTTP.start(uri.host, uri.port, :use_ssl => uri.scheme == 'https') do |http|
        http.request(request)
    end

    response.body
  end
end


:result

In [21]:
#vfg = VideoFaceRecog.new('fd39a67f3d8e46c094ac51078b49d909')
#vfg.start('./redcarpet.mp4')

"https://westus.api.cognitive.microsoft.com/video/v1.0/operations/9f35f91d-61f6-400c-a23e-3c9e818673ad"

In [3]:
vfg = VideoFaceRecog.new('fd39a67f3d8e46c094ac51078b49d909')
retval = vfg.result("https://westus.api.cognitive.microsoft.com/video/v1.0/operations/9f35f91d-61f6-400c-a23e-3c9e818673ad")
nil

In [5]:
rethash = JSON.parse retval
nil

In [6]:
res = JSON.parse rethash['processingResult'], symbolize_names: true
nil

In [14]:
res.keys

[:version, :timescale, :offset, :framerate, :width, :height, :fragments, :facesDetected]

In [20]:
res[:fragments].first.keys

[:start, :duration, :interval, :events]

In [21]:
res[:fragments].first[:interval].class

Fixnum

In [23]:
res[:fragments].first[:events].first

[{:id=>0, :x=>0.451172, :y=>0.298611, :width=>0.113281, :height=>0.201389}]

In [46]:
res[:fragments].first[:events].first

[{:id=>0, :x=>0.451172, :y=>0.298611, :width=>0.113281, :height=>0.201389}]

In [29]:
res[:fragments].first[:events].last

[{:id=>0, :x=>0.460938, :y=>0.253472, :width=>0.0761719, :height=>0.135417}, {:id=>1, :x=>0.695313, :y=>0.263889, :width=>0.0625, :height=>0.111111}, {:id=>2, :x=>0.220703, :y=>0.215278, :width=>0.0683594, :height=>0.121528}]

In [105]:
res[:fragments][1][:duration]

30

In [155]:
require 'daru'
require 'daru_plotting_plotly'

Daru.plotting_library = :plotly

twod_array = res[:fragments]&.map do |fragment|
  fragment[:events]&.map do |event|
    event.map do |face|
      face[:id]
    end
  end
end.flatten(1).map do |face_ids|
  if face_ids.nil?
    []
  else
    face_ids
  end
end.map do |face_ids|
  (0..39).to_a.map do |i|
    if face_ids.include?(i)
      i
    else
      nil
    end
  end
end.transpose

hash = twod_array.zip((0..39).to_a).map do |arr, ind|
  [ind.to_s, arr]
end.to_h

df = Daru::DataFrame.new(hash)
df.add_vector :time, df.index.to_a.map { |t| t.to_f / 15.to_f }
df.plot(x: :time, y: (0..39).to_a).show

#<Plotly::Offline::HTML:0x007fb18cb52d50 @id="4c88095d-9395-4747-93e7-61d4f7962131", @data=[{:x=>[0.0, 0.06666666666666667, 0.13333333333333333, 0.2, 0.26666666666666666, 0.3333333333333333, 0.4, 0.4666666666666667, 0.5333333333333333, 0.6, 0.6666666666666666, 0.7333333333333333, 0.8, 0.8666666666666667, 0.9333333333333333, 1.0, 1.0666666666666667, 1.1333333333333333, 1.2, 1.2666666666666666, 1.3333333333333333, 1.4, 1.4666666666666666, 1.5333333333333334, 1.6, 1.6666666666666667, 1.7333333333333334, 1.8, 1.8666666666666667, 1.9333333333333333, 2.0, 2.066666666666667, 2.1333333333333333, 2.2, 2.2666666666666666, 2.3333333333333335, 2.4, 2.466666666666667, 2.533333333333333, 2.6, 2.6666666666666665, 2.7333333333333334, 2.8, 2.8666666666666667, 2.933333333333333, 3.0, 3.066666666666667, 3.1333333333333333, 3.2, 3.2666666666666666, 3.3333333333333335, 3.4, 3.466666666666667, 3.533333333333333, 3.6, 3.6666666666666665, 3.7333333333333334, 3.8, 3.8666666666666667, 3.933333333333333, 4.0, 4.066666666666666, 4.133333333333334, 4.2, 4.266666666666667, 4.333333333333333, 4.4, 4.466666666666667, 4.533333333333333, 4.6, 4.666666666666667, 4.733333333333333, 4.8, 4.866666666666666, 4.933333333333334, 5.0, 5.066666666666666, 5.133333333333334, 5.2, 5.266666666666667, 5.333333333333333, 5.4, 5.466666666666667, 5.533333333333333, 5.6, 5.666666666666667, 5.733333333333333, 5.8, 5.866666666666666, 5.933333333333334, 6.0, 6.066666666666666, 6.133333333333334, 6.2, 6.266666666666667, 6.333333333333333, 6.4, 6.466666666666667, 6.533333333333333, 6.6, 6.666666666666667, 6.733333333333333, 6.8, 6.866666666666666, 6.933333333333334, 7.0, 7.066666666666666, 7.133333333333334, 7.2, 7.266666666666667, 7.333333333333333, 7.4, 7.466666666666667, 7.533333333333333, 7.6, 7.666666666666667, 7.733333333333333, 7.8, 7.866666666666666, 7.933333333333334, 8.0, 8.066666666666666, 8.133333333333333, 8.2, 8.266666666666667, 8.333333333333334, 8.4, 8.466666666666667, 8.533333333333333, 8.6, 8.666666666666666, 8.733333333333333, 8.8, 8.866666666666667, 8.933333333333334, 9.0, 9.066666666666666, 9.133333333333333, 9.2, 9.266666666666667, 9.333333333333334, 9.4, 9.466666666666667, 9.533333333333333, 9.6, 9.666666666666666, 9.733333333333333, 9.8, 9.866666666666667, 9.933333333333334, 10.0, 10.066666666666666, 10.133333333333333, 10.2, 10.266666666666667, 10.333333333333334, 10.4, 10.466666666666667, 10.533333333333333, 10.6, 10.666666666666666, 10.733333333333333, 10.8, 10.866666666666667, 10.933333333333334, 11.0, 11.066666666666666, 11.133333333333333, 11.2, 11.266666666666667, 11.333333333333334, 11.4, 11.466666666666667, 11.533333333333333, 11.6, 11.666666666666666, 11.733333333333333, 11.8, 11.866666666666667, 11.933333333333334, 12.0, 12.066666666666666, 12.133333333333333, 12.2, 12.266666666666667, 12.333333333333334, 12.4, 12.466666666666667, 12.533333333333333, 12.6, 12.666666666666666, 12.733333333333333, 12.8, 12.866666666666667, 12.933333333333334, 13.0, 13.066666666666666, 13.133333333333333, 13.2, 13.266666666666667, 13.333333333333334, 13.4, 13.466666666666667, 13.533333333333333, 13.6, 13.666666666666666, 13.733333333333333, 13.8, 13.866666666666667, 13.933333333333334, 14.0, 14.066666666666666, 14.133333333333333, 14.2, 14.266666666666667, 14.333333333333334, 14.4, 14.466666666666667, 14.533333333333333, 14.6, 14.666666666666666, 14.733333333333333, 14.8, 14.866666666666667, 14.933333333333334, 15.0, 15.066666666666666, 15.133333333333333, 15.2, 15.266666666666667, 15.333333333333334, 15.4, 15.466666666666667, 15.533333333333333, 15.6, 15.666666666666666, 15.733333333333333, 15.8, 15.866666666666667, 15.933333333333334, 16.0, 16.066666666666666, 16.133333333333333, 16.2, 16.266666666666666, 16.333333333333332, 16.4, 16.466666666666665, 16.533333333333335, 16.6, 16.666666666666668, 16.733333333333334, 16.8, 16.866666666666667, 16.933333333333334, 17.0, 17.066666666666666, 17.133333333333333, 17.2, 17.266666666666666, 17.333333333333332, 17.4, 17.466666

In [168]:
res[:fragments]&.map do |fragment|
  fal = fragment[:events]&.map do |event|
    [event.first, event.last]
  end
  unless fal.nil?
    fal = fal.transpose
    fal[0].zip(fal[1].drop(1)).map do |f,n|
      if !f.nil? && !n.nil?
        f[:id] == n[:id]
      else
        nil
      end
    end
  end
end

[[true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, false, false, false, false, false, false, false, false, false, false, nil], [false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, nil], [false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, nil], [false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, false, nil], [true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, true, nil